In [1]:
import pandas as pd
import dask.dataframe as dd

In [2]:
cols = ['Ligand SMILES', 'IC50 (nM)','KEGG ID of Ligand','Ki (nM)', 'Kd (nM)','EC50 (nM)']

In [3]:
allseq = ['BindingDB Target Chain  Sequence']+['BindingDB Target Chain  Sequence.{}'.format(j) for j in range(1,13)]

In [4]:
dtypes = {'BindingDB Target Chain  Sequence.{}'.format(i): 'object' for i in range(1,13)}

In [5]:
dtypes.update({'BindingDB Target Chain  Sequence': 'object',
           'IC50 (nM)': 'object',
           'KEGG ID of Ligand': 'object',
           'Ki (nM)': 'object',
           'Kd (nM)': 'object',
           'EC50 (nM)': 'object',
           'koff (s-1)': 'object'})

In [6]:
seq_name = 'BindingDB Target Chain  Sequence'

In [7]:
import tqdm.notebook

In [8]:
ddf = dd.read_csv('bindingdb/data/BindingDB_All.tsv',sep='\t',
                  error_bad_lines=False,
                  usecols=cols+allseq,
                  dtype=dtypes)

In [11]:
len(ddf[~ddf['BindingDB Target Chain  Sequence.1'].isnull()])/len(ddf[~ddf['BindingDB Target Chain  Sequence'].isnull()])

0.04789522637942933

In [18]:
# remove rows with more than one target
ddf_prune = ddf[ddf['BindingDB Target Chain  Sequence.1'].isnull()]
ddf_prune = ddf_prune.rename(columns={'BindingDB Target Chain  Sequence': 'seq'})

In [19]:
ddf_nonnull = ddf_prune[~ddf_prune.seq.isnull()].copy()

In [20]:
ddf_nonnull.head()

Ligand SMILES Ki (nM) IC50 (nM)  \
0      COc1cc2c(Nc3ccc(Br)cc3F)ncnc2cc1OCC1CCN(C)CC1    0.24       NaN   
1  O[C@@H]1[C@@H](O)[C@@H](Cc2ccccc2)N(C\C=C\c2cn...    0.25       NaN   
2  O[C@@H]1[C@@H](O)[C@@H](Cc2ccccc2)N(CC2CC2)C(=...    0.41       NaN   
3  OCCCCCCN1[C@H](Cc2ccccc2)[C@H](O)[C@@H](O)[C@@...     0.8       NaN   
4  OCCCCCN1[C@H](Cc2ccccc2)[C@H](O)[C@@H](O)[C@@H...    0.99       NaN   

  Kd (nM) EC50 (nM) KEGG ID of Ligand  \
0     NaN       NaN               NaN   
1     NaN       NaN               NaN   
2     NaN       NaN               NaN   
3     NaN       NaN               NaN   
4     NaN       NaN               NaN   

                                                 seq  \
0  PQITLWQRPLVTIKIGGQLKEALLDTGADDTVLEEMSLPGRWKPKM...   
1  PQITLWQRPLVTIKIGGQLKEALLDTGADDTVLEEMSLPGRWKPKM...   
2  PQITLWQRPLVTIKIGGQLKEALLDTGADDTVLEEMSLPGRWKPKM...   
3  PQITLWQRPLVTIKIGGQLKEALLDTGADDTVLEEMSLPGRWKPKM...   
4  PQITLWQRPLVTIKIGGQLKEALLDTGADDTVLEEMSLPGRWKPKM...   

  BindingDB Target Chain  Sequence.1 BindingDB Target Chain  Sequence.2  \
0                                NaN                                NaN   
1                                NaN                                NaN   
2                                NaN                                NaN   
3                                NaN                                NaN   
4                                NaN                                NaN   

  BindingDB Target Chain  Sequence.3 BindingDB Target Chain  Sequence.4  \
0                                NaN                                NaN   
1                                NaN                                NaN   
2                                NaN                                NaN   
3                                NaN                                NaN   
4                                NaN                                NaN   

  BindingDB Target Chain  Sequence.5 BindingDB Target Chain  Sequence.6  \
0                                NaN                                NaN   
1                                NaN                                NaN   
2                                NaN                                NaN   
3                                NaN                                NaN   
4                                NaN                                NaN   

  BindingDB Target Chain  Sequence.7 BindingDB Target Chain  Sequence.8  \
0                                NaN                                NaN   
1                                NaN                                NaN   
2                                NaN                                NaN   
3                                NaN                                NaN   
4                                NaN                                NaN   

  BindingDB Target Chain  Sequence.9 BindingDB Target Chain  Sequence.10  \
0                                NaN                                 NaN   
1                                NaN                                 NaN   
2                                NaN                                 NaN   
3                                NaN                                 NaN   
4                                NaN                                 NaN   

  BindingDB Target Chain  Sequence.11 BindingDB Target Chain  Sequence.12  
0                                 NaN                                 NaN  
1                                 NaN                                 NaN  
2                                 NaN                                 NaN  
3                                 NaN                                 NaN  
4                                 NaN                                 NaN

In [21]:
len(ddf_nonnull)

2221761

In [22]:
from pint import UnitRegistry
import numpy as np
import re
ureg = UnitRegistry()

def to_uM(affinities):
    ic50, Ki, Kd, ec50 = affinities

    vals = []
        
    try:
        ic50 =  ureg(str(ic50)+'nM').m_as(ureg.uM)
        vals.append(ic50)
    except:
        pass

    try:
        Ki = ureg(str(Ki)+'nM').m_as(ureg.uM)
        vals.append(Ki)
    except:
        pass

    try:
        Kd = ureg(str(Kd)+'nM').m_as(ureg.uM)
        vals.append(Kd)
    except:
        pass

    try:
        ec50 =  ureg(str(ec50)+'nM').m_as(ureg.uM)
        vals.append(ec50)
    except:
        pass

    if len(vals) > 0:
        vals = np.array(vals)
        return np.mean(vals[~np.isnan(vals)])
    
    return None

In [23]:
df_nonnull = ddf_nonnull.compute()

In [24]:
from pandarallel import pandarallel
pandarallel.initialize()


INFO: Pandarallel will run on 32 workers.
INFO: Pandarallel will use Memory file system to transfer data between the main process and workers.


In [25]:
df_affinity = df_nonnull.copy()
df_affinity['affinity_uM'] = df_affinity[['IC50 (nM)', 'Ki (nM)', 'Kd (nM)','EC50 (nM)']].parallel_apply(to_uM,axis=1)

In [26]:
df_affinity[~df_affinity['affinity_uM'].isnull()].to_parquet('data/bindingdb.parquet')

In [27]:
import pandas as pd
df_affinity = pd.read_parquet('data/bindingdb.parquet')

In [28]:
len(df_affinity)

2219812

In [29]:
df_affinity.head()

Ligand SMILES Ki (nM) IC50 (nM)  \
0      COc1cc2c(Nc3ccc(Br)cc3F)ncnc2cc1OCC1CCN(C)CC1    0.24      None   
1  O[C@@H]1[C@@H](O)[C@@H](Cc2ccccc2)N(C\C=C\c2cn...    0.25      None   
2  O[C@@H]1[C@@H](O)[C@@H](Cc2ccccc2)N(CC2CC2)C(=...    0.41      None   
3  OCCCCCCN1[C@H](Cc2ccccc2)[C@H](O)[C@@H](O)[C@@...     0.8      None   
4  OCCCCCN1[C@H](Cc2ccccc2)[C@H](O)[C@@H](O)[C@@H...    0.99      None   

  Kd (nM) EC50 (nM) KEGG ID of Ligand  \
0    None      None              None   
1    None      None              None   
2    None      None              None   
3    None      None              None   
4    None      None              None   

                                                 seq  \
0  PQITLWQRPLVTIKIGGQLKEALLDTGADDTVLEEMSLPGRWKPKM...   
1  PQITLWQRPLVTIKIGGQLKEALLDTGADDTVLEEMSLPGRWKPKM...   
2  PQITLWQRPLVTIKIGGQLKEALLDTGADDTVLEEMSLPGRWKPKM...   
3  PQITLWQRPLVTIKIGGQLKEALLDTGADDTVLEEMSLPGRWKPKM...   
4  PQITLWQRPLVTIKIGGQLKEALLDTGADDTVLEEMSLPGRWKPKM...   

  BindingDB Target Chain  Sequence.1 BindingDB Target Chain  Sequence.2  \
0                               None                               None   
1                               None                               None   
2                               None                               None   
3                               None                               None   
4                               None                               None   

  BindingDB Target Chain  Sequence.3 BindingDB Target Chain  Sequence.4  \
0                               None                               None   
1                               None                               None   
2                               None                               None   
3                               None                               None   
4                               None                               None   

  BindingDB Target Chain  Sequence.5 BindingDB Target Chain  Sequence.6  \
0                               None                               None   
1                               None                               None   
2                               None                               None   
3                               None                               None   
4                               None                               None   

  BindingDB Target Chain  Sequence.7 BindingDB Target Chain  Sequence.8  \
0                               None                               None   
1                               None                               None   
2                               None                               None   
3                               None                               None   
4                               None                               None   

  BindingDB Target Chain  Sequence.9 BindingDB Target Chain  Sequence.10  \
0                               None                                None   
1                               None                                None   
2                               None                                None   
3                               None                                None   
4                               None                                None   

  BindingDB Target Chain  Sequence.11 BindingDB Target Chain  Sequence.12  \
0                                None                                None   
1                                None                                None   
2                                None                                None   
3                                None                                None   
4                                None                                None   

   affinity_uM  
0      0.00024  
1      0.00025  
2      0.00041  
3      0.00080  
4      0.00099

In [30]:
len(df_affinity)

2219812

In [31]:
len(df_affinity[~df_affinity['affinity_uM'].isnull()])

2219812

In [25]:
import rdkit.Chem as Chem

In [27]:
df_pdb = df[~df['PDB ID(s) for Ligand-Target Complex'].isnull()][['PDB ID(s) for Ligand-Target Complex','Ligand SMILES']]

In [28]:
def make_canonical(smi):
    return Chem.MolToSmiles(Chem.MolFromSmiles(smi))

df_pdb['can_smiles'] = df_pdb['Ligand SMILES'].apply(make_canonical)

In [29]:
df_pdb

PDB ID(s) for Ligand-Target Complex  \
0                                                     2IVU   
29                                                    1HWR   
34                                6DGY,6DH1,6DH4,6DH7,3O99   
129                     1MES,1MEU,1MET,1BVG,1BVE,3JVW,1QBS   
130                                         1MER,1DMP,1RQ9   
...                                                    ...   
2333375  1MUI,2RKG,2RKF,1RV7,2Q5K,2O4S,6DJ1,6DJ2,3OGQ,2...   
2333376  4NPT,4DQH,4DQE,5E5J,3JW2,6OPU,6OPX,2HS2,2HS1,2...   
2333380                                6EKZ,1DY4,5FUK,6PS5   
2333384                                6EKZ,1DY4,5FUK,6PS5   
2333385                                          6A60,3DCT   

                                             Ligand SMILES  \
0            COc1cc2c(Nc3ccc(Br)cc3F)ncnc2cc1OCC1CCN(C)CC1   
29       O[C@@H]1[C@@H](O)[C@@H](Cc2ccccc2)N(CC=C)C(=O)...   
34       CC[C@H](C)CN(C[C@@H](O)[C@H](Cc1ccccc1)NC(=O)O...   
129      OCc1ccc(CN2[C@H](Cc3ccccc3)[C@H](O)[C@@H](O)[C...   
130      Nc1cccc(CN2[C@H](Cc3ccccc3)[C@H](O)[C@@H](O)[C...   
...                                                    ...   
2333375  CC(C)[C@H](N1CCCNC1=O)C(=O)N[C@H](C[C@H](O)[C@...   
2333376  CC(C)CN(C[C@@H](O)[C@H](Cc1ccccc1)NC(=O)O[C@H]...   
2333380                        CC(C)NCC(O)COc1cccc2ccccc12   
2333384                        CC(C)NCC(O)COc1cccc2ccccc12   
2333385  CC(C)c1onc(c1COc1ccc(\C=C\c2cccc(c2)C(O)=O)c(C...   

                                                can_smiles  
0            COc1cc2c(Nc3ccc(Br)cc3F)ncnc2cc1OCC1CCN(C)CC1  
29       C=CCN1C(=O)N(CC=C)[C@H](Cc2ccccc2)[C@H](O)[C@@...  
34       CC[C@H](C)CN(C[C@@H](O)[C@H](Cc1ccccc1)NC(=O)O...  
129      O=C1N(Cc2ccc(CO)cc2)[C@H](Cc2ccccc2)[C@H](O)[C...  
130      Nc1cccc(CN2C(=O)N(Cc3cccc(N)c3)[C@H](Cc3ccccc3...  
...                                                    ...  
2333375  Cc1cccc(C)c1OCC(=O)N[C@@H](Cc1ccccc1)[C@@H](O)...  
2333376  CC(C)CN(C[C@@H](O)[C@H](Cc1ccccc1)NC(=O)O[C@H]...  
2333380                        CC(C)NCC(O)COc1cccc2ccccc12  
2333384                        CC(C)NCC(O)COc1cccc2ccccc12  
2333385  CC(C)c1onc(-c2c(Cl)cccc2Cl)c1COc1ccc(/C=C/c2cc...  

[123385 rows x 3 columns]